In [36]:
import pandas as pd
import os
import matplotlib.pyplot as plt
import pandas as pd
import plotly.express as px
import plotly.express as px
import plotly.express as px
import numpy as np
url= os.path.join(os.getcwd(), "data", "base_transacciones.xlsx")
data = pd.read_excel(url, sheet_name="Sheet 1")
var='Transaccion'

In [39]:
import plotly.express as px
import numpy as np
fig = px.scatter(x=data.ID, y=data[var])
mediana = data[var].median()
# METODO TRIMMER:
Q1 = np.percentile(data[var], 25)
Q3 = np.percentile(data[var], 75)
IQR = Q3 - Q1
lower_bound = Q1 - 1.5 * IQR
upper_bound = Q3 + 1.5 * IQR
data_no_outliers = data[(data[var] >= lower_bound) & (data[var] <= upper_bound)]
mean_no_outliers = data_no_outliers[var].mean()
data[var] = np.where(
    (data[var] < lower_bound) | (data[var] > upper_bound),
    mean_no_outliers,
    data[var]
)

fig.update_layout(
    width=1000,  # Ancho en píxeles (equivalente a 10 en Matplotlib)
    height=500,  # Alto en píxeles (equivalente a 5 en Matplotlib)
    title_x=0.5  # Centrar el título
)
fig.show()


In [40]:

def get_clean_data(method='min',var='Altura'): 
    fig = px.scatter(x=data.ID, y=data[var])
    mediana = data[var].median()
    fig.add_shape(
        type='line',x0=data['ID'].min(), x1=data['ID'].max(), 
        y0=mediana, y1=mediana, line=dict(color='red', width=2, dash='dash'),  
        name='Mediana'  )
    fig.update_layout(width=1000, height=500,title_x=0.5
                      )
    ## RANGO INTERQUARTIL 
    Q1 = np.percentile(data[var], 25)
    Q3 = np.percentile(data[var], 75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    ## GENERAR DATA CORREGIDA 
    data['Altura_original']=data[var]
    data_no_outliers = data[(data[var] >= lower_bound) & (data[var] <= upper_bound)]
    if method=='min':
        min_no_outliers = data_no_outliers[var].min()
        print(method+" "+str(min_no_outliers))
        data[var] = np.where(
            (data[var] < lower_bound) | (data[var] > upper_bound),
            min_no_outliers,
            data[var]
        )

    elif method=='max':
        max_no_outliers = data_no_outliers[var].max()
        print(method+" "+str(max_no_outliers))
        data[var] = np.where(
            (data[var] < lower_bound) | (data[var] > upper_bound),
            max_no_outliers,
            data[var]
        )
    elif method=='mean':
        mean_no_outliers = data_no_outliers[var].mean()
        print(method+" "+str(mean_no_outliers))
        data[var] = np.where(
            (data[var] < lower_bound) | (data[var] > upper_bound),
            mean_no_outliers,
            data[var]
        )
    elif method=='std':
        std_no_outliers = data_no_outliers[var].std()
        print(method+" "+str(std_no_outliers))
        data[var] = np.where(
            (data[var] < lower_bound) | (data[var] > upper_bound),
            std_no_outliers,
            data[var]
        )
    else:
        pass

    ### Agregar limites 
    fig.add_shape(
        type='line',
        x0=data['ID'].min(), x1=data['ID'].max(),
        y0=lower_bound, y1=lower_bound,
        line=dict(color='black', width=2, dash='dot'),
        name='Límite Inferior'
    )

    # Agregar la línea del límite superior (upper_bound)
    fig.add_shape(
        type='line',
        x0=data['ID'].min(), x1=data['ID'].max(),
        y0=upper_bound, y1=upper_bound,
        line=dict(color='black', width=2, dash='dot'),
        name='Límite Superior')
    
    fig.show()
    return(data)

In [42]:
for i in ['min','max','std','mean','ori']:
    get_clean_data(method=i,var='Transaccion')

min 2319.30316324611


max 7706.23342160763


std 975.4318506944957


mean 5006.0517456769185


In [44]:
import numpy as np
import pandas as pd
from scipy.spatial.distance import mahalanobis
from scipy.stats import chi2

# Crear datos simulados
np.random.seed(42)
data = pd.DataFrame({
    'Variable1': np.random.normal(50, 10, 100),  # Media 50, Desviación estándar 10
    'Variable2': np.random.normal(30, 5, 100)   # Media 30, Desviación estándar 5
})

# Calcular la media y la matriz de covarianza
mean = data.mean().values
cov_matrix = np.cov(data.values, rowvar=False)
inv_cov_matrix = np.linalg.inv(cov_matrix)

# Calcular la distancia de Mahalanobis para cada punto
data['Mahalanobis'] = data.apply(lambda row: mahalanobis(row.values, mean, inv_cov_matrix), axis=1)

# Calcular el valor crítico de Chi-cuadrado para un nivel de confianza del 95%
p_value = 0.80
chi2_critical = chi2.ppf(p_value, df=data.shape[1] - 1)

# Identificar valores atípicos
data['Outlier'] = data['Mahalanobis'] > np.sqrt(chi2_critical)

# Mostrar los resultados
print(data)

# Visualizar con un gráfico interactivo
import plotly.express as px
fig = px.scatter(
    data,
    x='Variable1',
    y='Variable2',
    color='Outlier',
    title='Distancia de Mahalanobis y Valores Atípicos',
    labels={'Outlier': 'Es Atípico'},
    template='plotly_white'
)
fig.show()

    Variable1  Variable2  Mahalanobis  Outlier
0   54.967142  22.923146     1.576119    False
1   48.617357  27.896773     0.475584    False
2   56.476885  28.286427     0.871211    False
3   65.230299  25.988614     1.897647     True
4   47.658466  29.193571     0.257721    False
..        ...        ...          ...      ...
95  35.364851  31.926587     1.507707    False
96  52.961203  25.580713     1.000635    False
97  52.610553  30.768626     0.446373    False
98  50.051135  30.291044     0.131787    False
99  47.654129  24.285149     1.261484    False

[100 rows x 4 columns]
